In [2]:
import numpy as np
from numba import njit
from functools import partial

import pandas as pd
import vectorbt as vbt
import vectorbt as vbt
from vectorbt.utils.colors import adjust_opacity
from vectorbt.utils.enum_ import map_enum_fields
from vectorbt.base.reshape_fns import broadcast, flex_select_auto_nb, to_2d_array
from vectorbt.portfolio.enums import SizeType, Direction, NoOrder, OrderStatus, OrderSide
from vectorbt.portfolio import nb

import talib
import sys
import os
function_essential_path = r"H:\Desktop\Environement_Trading_Developement\FunctionEssential"
function_s_score_path = r'H:\Desktop\Environement_Trading_Developement\Indicateur'
sys.path.append(function_essential_path)
sys.path.append(function_s_score_path)
import utils as us
import s_score as score

In [3]:
##FONCTION##

In [4]:
##FONCTION LOGIQUE SIGNALS##


def entries_trades(close,sscore,bb_upper,bb_lower,adx,seuil_sscore,seuil_adx):

    entries_long  = [False] * len(close)
    entries_short = [False] * len(close)
    count_between_trade = 15
    for idx in range(len(close)):
        #Activation de la recherche / Filtre
        if (adx.iloc[idx] < seuil_adx) and (count_between_trade >= 15):

            if (sscore.iloc[idx] > seuil_sscore) and (close.iloc[idx] > bb_upper.iloc[idx]):
                entries_short[idx] = True
                count_between_trade = 0
            if (sscore.iloc[idx] < -seuil_sscore) and (close.iloc[idx] < bb_lower.iloc[idx]):
                entries_long[idx] = True
                count_between_trade = 0

        count_between_trade += 1
    return entries_long,entries_short


In [5]:
##INDICATEUR FACTORY##

In [149]:
from numba import njit
import numpy as np
import vectorbt as vbt
# Assurez-vous d'avoir importé nb, Direction, OrderStatus, NoOrder, etc.

@njit
def pre_sim_func_nb(c):
    entry_price = np.full(c.target_shape[1], np.nan, dtype=np.float64)  
    atr_value = np.full(c.target_shape[1], np.nan, dtype=np.float64)  
    mu_value = np.full(c.target_shape[1], np.nan, dtype=np.float64)  
    return (entry_price,atr_value,mu_value,)

@njit
def order_func_nb(c, entry_price, atr_value,mu_value,long, short, stop_loss, take_profit, size):
    price_now = nb.get_elem_nb(c, c.close)
    entry_long_now = nb.get_elem_nb(c, long)
    entry_short_now = nb.get_elem_nb(c, short)

    if entry_long_now:
        if c.position_now == 0:
            return nb.order_nb(
                size[c.col], 
                price=price_now,
                direction=Direction.LongOnly,
                fees=0.0005
            )
        elif c.position_now < 0:
            return nb.order_nb(
                -size[c.col],  
                price=price_now,
                direction=Direction.ShortOnly,
                fees=0.0005
            )  

    if entry_short_now:
        if c.position_now == 0:
            return nb.order_nb(
                size[c.col], 
                price=price_now,
                direction=Direction.ShortOnly,
                fees=0.0005
            )
        elif c.position_now > 0:
            return nb.order_nb(
                -size[c.col],  
                price=price_now,
                direction=Direction.LongOnly,
                fees=0.0005
            )

    if c.position_now > 0:
        SL = entry_price[c.col] - (3*atr_value[c.col])
        TP = entry_price[c.col] + (5*atr_value[c.col])
        
        if price_now >= TP:
            return nb.order_nb(
                -size[c.col],
                price=TP,
                direction=Direction.LongOnly,
                fees=0.0005
            )
        elif price_now <= SL:
            return nb.order_nb(
                -size[c.col],
                price=SL,
                direction=Direction.LongOnly,
                fees=0.0005
            )

    if c.position_now < 0:
        SL = entry_price[c.col] + (3*atr_value[c.col])
        TP = entry_price[c.col] - (5*atr_value[c.col])
        if price_now >= SL:
            return nb.order_nb(
                -size[c.col],
                price=SL,
                direction=Direction.ShortOnly,
                fees=0.0005
            )
        elif price_now <= TP:
            return nb.order_nb(
                -size[c.col],
                price=TP,
                direction=Direction.ShortOnly,
                fees=0.0005
            )

    return NoOrder

@njit
def post_order_func_nb(c, entry_price,atr_value,mu_value,atr,mu):
    if c.order_result.status == OrderStatus.Filled:
        entry_price[c.col] = c.order_result.price
        atr_value[c.col] = atr[c.i,c.col]
        mu_value[c.col] = mu[c.i,c.col]
        
class Strategie:
    def __init__(self, data, tickers, frequence_exec, frequence, multitimeframe):
        self.data = data
        self.tickers = tickers
        self.frequence_exec = frequence_exec
        self.frequences = frequence
        self.multitimeframe = multitimeframe

    def backtest(self, sscore, datah4):
        # Préparation des DataFrames
        entries_long_df = pd.DataFrame()
        entries_short_df = pd.DataFrame()
        close_df = pd.DataFrame()
        datetime_df = pd.DataFrame()

        for ticker in self.tickers:
            data = self.data[ticker]

            data_reset = data.reset_index()
            datetime = data_reset['Datetime']




            adx = talib.ADX(data['high'], data['low'], data['close'], timeperiod=14)



            
            atr = vbt.ATR.run(data['close'], data['high'], data['low'], window=14).atr
            mu = sscore[ticker]['mu_vals']
            sscore_ajuster = sscore[ticker]['adjusted_s_scores_vol']

            sma = talib.SMA(data['close'], timeperiod=20)
            stddev = talib.STDDEV(data['close'], timeperiod=20, nbdev=1)
            upper_band = sma + (stddev * 2)
            lower_band = sma - (stddev * 2)

            long, short = entries_trades(data['close'], sscore_ajuster, upper_band, lower_band, adx, 3, 25)
            long = pd.Series(long, index=data['close'].index)
            short = pd.Series(short, index=data['close'].index)
            us.print_trades(0, long, short, None, None, data)

            long = long.reset_index(drop=True)
            short = short.reset_index(drop=True)
            close = data['close'].reset_index(drop=True)
            datetime = datetime.reset_index(drop=True)

            entries_long_df[ticker] = long
            entries_short_df[ticker] = short
            close_df[ticker] = close
            datetime_df[ticker] = datetime

        close_df = close_df.replace(0, None).fillna(method='ffill')

        capital = 100000
        risk_per_trade = 0.01
        position_value = capital * risk_per_trade
        size = np.array([position_value / close_df.iloc[-1, i] for i in range(len(self.tickers))])

        # Préparer atr et mu comme matrices colonne
        atr = atr.values.reshape(-1, 1)
        mu = mu.values.reshape(-1, 1)
        size = size.astype(float)


        stop_loss = np.array([0.04] * len(self.tickers))  
        take_profit = np.array([0.02] * len(self.tickers))  

        portfolio = vbt.Portfolio.from_order_func(
            close_df,  
            order_func_nb,  
            entries_long_df.values,  
            entries_short_df.values,  
            stop_loss,  
            take_profit,  
            size,  
            freq=self.frequence_exec,  
            init_cash=100000,  # Ajout du capital initial
            pre_sim_func_nb=pre_sim_func_nb,  
            post_order_func_nb=post_order_func_nb,
            post_order_args=( 
                atr,
                mu
            ),
            broadcast_named_args=dict(  
                long=entries_long_df.values,  
                short=entries_short_df.values,  
                stop_loss=stop_loss,  
                take_profit=take_profit,  
                size=size  
            )
        )

        us.rapport_backtest(portfolio, close_df, datetime_df, self.tickers)
        return portfolio


In [147]:
##UTILISATION DE LA STRAT##
tickers = ["GPDUSD"]
DATAH1 = us.get_data_forex(tickers,'H1',"2000-01-01","2011-01-01")
DATAH4 = us.get_data_forex(tickers,'D1',"2000-01-01","2011-01-01")
s_score_value = {}
for ticker in tickers:
    data_traitement = DATAH1[ticker]
    nb_nan = data_traitement['close'].isna().sum()
    close = data_traitement['close'].dropna()
    close_without_index = close.reset_index()
    result = score.mean_reversion(close, close_without_index['Datetime'], 85, "VOL", 0.5, "EGARCH")
    result_df = pd.DataFrame({
        's_score_value': result[0],
        'adjusted_s_scores_vol': result[1],
        'theta_vals': result[2],
        'mu_vals': result[3],
        'sigma_vals': result[4]
    })
    nan_rows = pd.DataFrame([[float('nan')] * result_df.shape[1]] * nb_nan, columns=result_df.columns)
    result_df = pd.concat([result_df, nan_rows], ignore_index=True)

    s_score_value[ticker] = result_df

Estimation des paramètres OU:   0%|          | 0/51945 [00:00<?, ?it/s]

  0%|          | 0/51945 [00:00<?, ?it/s]

H:\Desktop\Environement_Trading_Developement\Indicateur\s_score.py:31: RuntimeWarning:

invalid value encountered in sqrt

c:\Users\CYTech Student\AppData\Local\Programs\Python\Python311\Lib\site-packages\arch\univariate\base.py:768: ConvergenceWarning:

The optimizer returned code 4. The message is:
Inequality constraints incompatible
See scipy.optimize.fmin_slsqp for code meaning.


Calcul de la volatilité conditionnelle: 100%|██████████| 52030/52030 [00:00<00:00, 67628.28it/s]


52029


C:\Users\CYTech Student\AppData\Local\Temp\ipykernel_10200\775336598.py:20: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.



In [150]:
strat = Strategie(DATAH1,tickers,"60m","60m",0)
port = strat.backtest(s_score_value,DATAH4)

C:\Users\CYTech Student\AppData\Local\Temp\ipykernel_10200\3718068859.py:150: FutureWarning:

DataFrame.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.




------------------------------------------------------------------DETAILS : GPDUSD-----------------------------------------------------------------

Total Return : -0.28%
Benchmark return : 0.87%
CAGR : -0.05%
Volatility : 0.05%
Sharpe Ratio : -0.9
Benchmark sharpe ratio : 0.02
Max Drawdown: -0.3%
Calmar Ratio : -0.16
Beta : -0.0


Total trades : 124
Total long trades 51
Total short trades 73
Win rate : 0.37%
Wining streak : 5.0
Loosing streak : 11.0
Average winning trade : 1.0%
Average losing trade : -1.0%
Profit factor : 0.62
Expectancy : -2.25%



 -> Average duration trades (jour) : 4.28




--------------------------------------------------------------------------------------------------------------------------------------------------

